In [0]:
training_data = spark.read.parquet("/databricks-datasets/news20.binary/data-001/training").select("text", "topic")
training_data.cache()
display(training_data)
training_data.printSchema()

text topic From: mouse@thunder.mcrcim.mcgill.edu (der Mouse) Subject: Re: Creating 8 bit windows on 24 bit display.. How? Organization: McGill Research Centre for Intelligent Machines Lines: 59 In article <1993Apr16.093209.25719@fwi.uva.nl>, stolk@fwi.uva.nl (Bram) writes: > I am using an X server that provides 3 visuals: PseudoColor 8 bit, > Truecolor 24 bit and DirectColor 24 bit. Lucky dog... :-) > A problem occurs when I try to create a window with a visual that is > different from the visual of the parent (which uses the default > visual which is TC24). > In the Xlib reference guide from 'O reilly one can read in the > section about XCteateWindow, something like: > In the current implementation of X11: When using a visual other > than the parent's, be sure to create or find a suitable colourmap > which is to be used in the window attributes when creating, or > else a BadMatch occurs. > This warning, strangely enough, is only mentioned in the newer > editions of the X11R5 guides. It applies with equal force to earlier versions. Presumably only recently did the author(s) decide it was important enough to mention. The necessity it refers to has always been there, but it's been implicit in the way CreateWindow requests default some attributes of the new window. > However, even if I pass along a suitable colourmap, I still get a > BadMatch when I create a window with a non-default visual. > attr.colormap = cmap; > win = XCreateWindow( [...] > CopyFromParent, /* border width */ > 8, /* depth */ > InputOutput, /* class */ > vinfo.visual, /* visual */ > CWColormap, > &attr > ); This is because the warning you read is incomplete. You have to provide not only a colormap but also a border. The default border is CopyFromParent, which is not valid when the window's depth doesn't match its parent's. Specify a border-pixmap of the correct depth, or a border-pixel, and the problem should go away. There is another problem: I can't find anything to indicate that CopyFromParent makes any sense as the border_width parameter to XCreateWindow. Your Xlib implementation probably defines CopyFromParent as zero, to simplify the conversion to wire format, so you are unwittingly asking for a border width of zero, due to the Xlib implementation not providing stricter type-checking. (To be fair, I'm not entirely certain it's possible for Xlib to catch this.) der Mouse mouse@mcrcim.mcgill.edu comp.windows.x From: geb@cs.pitt.edu (Gordon Banks) Subject: Re: ORGAN DONATION AND TRANSPLANTATION FACT SHEET Reply-To: geb@cs.pitt.edu (Gordon Banks) Organization: Univ. of Pittsburgh Computer Science Lines: 26 In article <1993Apr13.150018.641@lmpsbbs.comm.mot.com> dougb@ecs.comm.mot.com writes: >My wife cannot donate blood because she has been to a malarial region >in the past three years. In fact, she tried to have her bone marrow >typed and they wouldn't even do that! Why? > The FDA, I believe. Rules say no blood or blood products donations from anyone who has been in a malarial area for 3 years. I was a platelet donor until my Thailand trip and my blood bank was very disappointed to find out they couldn't use me for 3 years. > >When the secretary of state asked me if I wanted to donate my >organs I said no because I figured that no one would want them >given my history. Was I correct? > Not necessarily. The same rules may not apply to organ donation as to blood donation. In fact, I'm sure they don't. -- ---------------------------------------------------------------------------- Gordon Banks N3JXP | "Skepticism is the chastity of the intellect, and geb@cadre.dsl.pitt.edu | it is shameful to surrender it too soon." ---------------------------------------------------------------------------- sci.med From: tclock@orion.oac.uci.edu (Tim Clock) Subject: Re: THE HAMAS WAY of DEATH Nntp-Posting-Host: orion.oac.uci.edu Organization: University of California, Irvine Lines: 15 In article <1993Apr17.160731.3178@nntpd.lkg.dec.com> alaa@peewee.unx.dec.com (Alaa Zeineldin

root
-- text: string (nullable = true)
-- topic: string (nullable = true)

In [0]:
from pyspark.ml.feature import StringIndexer, Tokenizer, HashingTF
label_indexer = StringIndexer(
inputCol="topic", 
outputCol="label", 
handleInvalid="keep")
tokenizer = Tokenizer(inputCol="text", outputCol="words")
hashing_tf = HashingTF(inputCol="words", outputCol="features")


In [0]:
from pyspark.ml.classification import DecisionTreeClassifier
classifier = DecisionTreeClassifier()

In [0]:
from pyspark.ml import Pipeline
pipeline = Pipeline(stages=[label_indexer, tokenizer, hashing_tf, classifier])


In [0]:
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
hyperparam_grid = ParamGridBuilder().addGrid(
hashing_tf.numFeatures, [500, 750, 1000]).build()
cv = CrossValidator(estimator=pipeline,
evaluator=MulticlassClassificationEvaluator(),
estimatorParamMaps=hyperparam_grid)

In [0]:
cv_model = cv.fit(training_data)
model = cv_model.bestModel

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [0]:
predictions = model.transform(training_data)
display(predictions)

text topic label words features rawPrediction probability prediction From: mouse@thunder.mcrcim.mcgill.edu (der Mouse) Subject: Re: Creating 8 bit windows on 24 bit display.. How? Organization: McGill Research Centre for Intelligent Machines Lines: 59 In article <1993Apr16.093209.25719@fwi.uva.nl>, stolk@fwi.uva.nl (Bram) writes: > I am using an X server that provides 3 visuals: PseudoColor 8 bit, > Truecolor 24 bit and DirectColor 24 bit. Lucky dog... :-) > A problem occurs when I try to create a window with a visual that is > different from the visual of the parent (which uses the default > visual which is TC24). > In the Xlib reference guide from 'O reilly one can read in the > section about XCteateWindow, something like: > In the current implementation of X11: When using a visual other > than the parent's, be sure to create or find a suitable colourmap > which is to be used in the window attributes when creating, or > else a BadMatch occurs. > This warning, strangely enough, is only mentioned in the newer > editions of the X11R5 guides. It applies with equal force to earlier versions. Presumably only recently did the author(s) decide it was important enough to mention. The necessity it refers to has always been there, but it's been implicit in the way CreateWindow requests default some attributes of the new window. > However, even if I pass along a suitable colourmap, I still get a > BadMatch when I create a window with a non-default visual. > attr.colormap = cmap; > win = XCreateWindow( [...] > CopyFromParent, /* border width */ > 8, /* depth */ > InputOutput, /* class */ > vinfo.visual, /* visual */ > CWColormap, > &attr > ); This is because the warning you read is incomplete. You have to provide not only a colormap but also a border. The default border is CopyFromParent, which is not valid when the window's depth doesn't match its parent's. Specify a border-pixmap of the correct depth, or a border-pixel, and the problem should go away. There is another problem: I can't find anything to indicate that CopyFromParent makes any sense as the border_width parameter to XCreateWindow. Your Xlib implementation probably defines CopyFromParent as zero, to simplify the conversion to wire format, so you are unwittingly asking for a border width of zero, due to the Xlib implementation not providing stricter type-checking. (To be fair, I'm not entirely certain it's possible for Xlib to catch this.) der Mouse mouse@mcrcim.mcgill.edu comp.windows.x 7.0 List(from:, mouse@thunder.mcrcim.mcgill.edu, (der, mouse), subject:, re:, creating, 8, bit, windows, on, 24, bit, display.., how?, organization:, mcgill, research, centre, for, intelligent, machines, lines:, 59, , in, article, <1993apr16.093209.25719@fwi.uva.nl>,, stolk@fwi.uva.nl, (bram), writes:, , >, i, am, using, an, x, server, that, provides, 3, visuals:, pseudocolor, 8, bit,, >, truecolor, 24, bit, and, directcolor, 24, bit., , lucky, dog..., :-), , >, a, problem, occurs, when, i, try, to, create, a, window, with, a, visual, that, is, >, different, from, the, visual, of, the, parent, (which, uses, the, default, >, visual, which, is, tc24)., , >, in, the, xlib, reference, guide, from, 'o, reilly, one, can, read, in, the, >, section, about, xcteatewindow,, something, like:, >, , , , , in, the, current, implementation, of, x11:, when, using, a, visual, other, >, , , , , than, the, parent's,, be, sure, to, create, or, find, a, suitable, colourmap, >, , , , , which, is, to, be, used, in, the, window, attributes, when, creating,, or, >, , , , , else, a, badmatch, occurs., , >, this, warning,, strangely, enough,, is, only, mentioned, in, the, newer, >, editions, of, the, x11r5, guides., , it, applies, with, equal, force, to, earlier, versions., , presumably, only, recently, did, the, author(s), decide, it, was, important, enough, to, mention., the, necessity, it, refers, to, has, always, been, there,, but, it's, been, implicit, in, the, way, createwindow, requests, default, some, attribute

In [0]:
%sh 
mkdir /tmp/mleap__serialized_pipilene

In [0]:
model_uri

Out[12]: 'jar:file://tmp/mleap__serialized_pipilene/serialized_pipeline.zip'

In [0]:
import mleap.pyspark
from mleap.pyspark.spark_support import SimpleSparkSerializer
model_path="/tmp/mleap__serialized_pipilene"
model_filename="serialized_pipeline.zip"
model_uri=f"jar:file:{model_path}/{model_filename}"
model.serializeToBundle(model_uri, predictions)


In [0]:
test_data = spark.read.parquet("/databricks-datasets/news20.binary/data-001/test").select("text", "topic")
test_data.cache()
display(test_data)

text topic From: marshall@csugrad.cs.vt.edu (Kevin Marshall) Subject: Re: Faith and Dogma Organization: Virginia Tech Computer Science Dept, Blacksburg, VA Lines: 96 NNTP-Posting-Host: csugrad.cs.vt.edu tgk@cs.toronto.edu (Todd Kelley) writes: >In light of what happened in Waco, I need to get something of my >chest. > >Faith and dogma are dangerous. > >Religion inherently encourages the implementation of faith and dogma, and >for that reason, I scorn religion. I don't necessarily disagree with your assertion, but I disagree with your reasoning. (Faith = Bad. Dogma = Bad. Religion -> (Faith ^ Dogma). Religion -> (Bad ^ Bad). Religion -> Bad.) Unfortunately, you never state why faith and dogma are dangerous. If you believe faith and dogma are dangerous because of what happened in Waco, you are missing the point. The Branch Davidians made the mistake of confusing the message with the messenger. They believed Koresh was a prophet, and therefore believed everything he said. The problem wasn't the religion, it was the followers. They didn't die because of faith and dogma, they died because of their zealotry (or, in the case of the children, the zealotry of their parents). >I have expressed this notion in the past. Some Christians debated >with me whether Christianity leaves any room for reasoning. I claimed >rationality is quelled out of Christianity by faith and dogma. So Christians are totally irrational? Irrational with respect to their religion only? What are you saying? One's belief in a Christian God does not make one totally irrational. I think I know what you were getting at, but I'd rather hear you expand on the subject. >A philosopher cannot be a Christian because a philosopher can change his mind, >whereas a Christian cannot, due to the nature of faith and dogma present >in any religion. Again, this statement is too general. A Christian is perfectly capable of being a philosopher, and absolutely capable of changing his/her mind. Faith in God is a belief, and all beliefs may change. Would you assert that atheists would make poor philosophers because they are predisposed to not believe in a God which, of course, may show unfair bias when studying, say, religion? >I claimed that a ``Christian philosopher'' is not a Christian, >but is a person whose beliefs at the moment correspond with those >of Christianity. Consider that a person visiting or guarding a prison >is not a prisoner, unless you define a prisoner simply to be someone >in a prison. >Can we define a prisoner to be someone who at the moment is in a prison? >Can we define a Christian to be someone who at the moment has Christian >beliefs? No, because if a person is free to go, he is not a prisoner. >Similarly, if a person is not constrained by faith and dogma, he is not >a Christian. So, Christianity is a prison, eh? Ever heard of parole? You have read far too much into this subject. A Christian is one who follows the religion based on the teachings of a man named Jesus Christ. Nowhere does this definition imply that one cannot change one's mind. In prison, however, you can't just decide to leave. One is voluntary, the other is not. The two are not compatible. >Religion is like the gun that doesn't kill anybody. Religion encourages >faith and dogma and although it doesn't directly condemn people, >it encourages the use of ``just because'' thinking. It is >``just because'' thinking that kills people. I prefer to think of religion as a water pistol filled with urine. 8^) Seriously, though, some (but certainly not all) religions do condemn groups of people. The common target is the "infidel," a curious being who is alternately an atheist, a non- , a person of a different race, or an Egyptian. 8^) Please explain how "just because" thinking kills people. (And please state more in your answer than "Waco.") >Of course, not all humans are capable of thought, and we'd still >have genocide and maybe even some mass suicide...but not as much. >I'm willing to bet on that. I'll s

In [0]:
import pandas as pd
wind_farm_data = pd.read_csv("https://github.com/dbczumar/model-registry-demo-notebook/raw/master/dataset/windfarm_data.csv", index_col=0)

In [0]:
training_data = pd.DataFrame(wind_farm_data["2014-01-01":"2018-01-01"])
training_data_x = training_data.drop(columns="power")
training_data_y = training_data["power"]
validation_data = pd.DataFrame(wind_farm_data["2018-01-01":"2019-01-01"])
validation_x= validation_data.drop(columns="power")
validation_y = validation_data["power"]

In [0]:
import tensorflow as tf
from tensorflow.keras.layers import Dense
from tensorflow.keras.models import Sequential
model = Sequential()
model.add(Dense(120, input_shape=( training_data_x.shape[-1],), activation="relu", name="hidden_layer"))
model.add(Dense(1))

In [0]:
import mlflow
import mlflow.keras
import mlflow.tensorflow
with mlflow.start_run():
  mlflow.tensorflow.autolog()
  model.compile(loss="mse", optimizer="adam")
  model.fit(training_data_x, training_data_y, epochs=100, batch_size=32, validation_split=.2)
  run_id = mlflow.active_run().info.run_id


Epoch 1/100
 1/37 [..............................] - ETA: 14s - loss: 13650072.0000WARNING:tensorflow:Callback method `on_train_batch_end` is slow compared to the batch time (batch time: 0.0010s vs `on_train_batch_end` time: 0.0038s). Check your callbacks.
29/37 [======================>.......] - ETA: 0s - loss: 10564938.4828 37/37 [==============================] - 1s 17ms/step - loss: 10327475.6053 - val_loss: 7010075.5000
Epoch 2/100
 1/37 [..............................] - ETA: 0s - loss: 9256918.000037/37 [==============================] - 0s 2ms/step - loss: 9103096.6579 - val_loss: 5787546.0000
Epoch 3/100
 1/37 [..............................] - ETA: 0s - loss: 8667707.000037/37 [==============================] - 0s 2ms/step - loss: 7767455.8816 - val_loss: 4857740.0000
Epoch 4/100
 1/37 [..............................] - ETA: 0s - loss: 7968288.000037/37 [==============================] - 0s 2ms/step - loss: 6206970.8947 - val_loss: 4506521.5000
Epoch 5/100
 1/37 [..............................] - ETA: 0s - loss: 4352164.000037/37 [==============================] - 0s 2ms/step - loss: 5468120.0921 - val_loss: 4548711.0000
Epoch 6/100
 1/37 [..............................] - ETA: 0s - loss: 7268968.000037/37 [==============================] - 0s 2ms/step - loss: 5595911.5132 - val_loss: 4584017.0000
Epoch 7/100
 1/37 [..............................] - ETA: 0s - loss: 3532997.000037/37 [==============================] - 0s 2ms/step - loss: 5188757.7697 - val_loss: 4589618.0000
Epoch 8/100
 1/37 [..............................] - ETA: 0s - loss: 7568635.000037/37 [==============================] - 0s 2ms/step - loss: 5723409.1711 - val_loss: 4563780.5000
Epoch 9/100
 1/37 [..............................] - ETA: 0s - loss: 7734266.000037/37 [==============================] - 0s 2ms/step - loss: 5366693.8289 - val_loss: 4507217.5000
Epoch 10/100
 1/37 [..............................] - ETA: 0s - loss: 2728920.000037/37 [==============================] - 0s 2ms/step - loss: 5309632.4868 - val_loss: 4495429.5000
Epoch 11/100
 1/37 [..............................] - ETA: 0s - loss: 2447444.250037/37 [==============================] - ETA: 0s - loss: 5149024.628437/37 [==============================] - 0s 3ms/step - loss: 5153472.0461 - val_loss: 4474770.5000
Epoch 12/100
 1/37 [..............................] - ETA: 0s - loss: 4590106.500037/37 [==============================] - 0s 2ms/step - loss: 5085719.7632 - val_loss: 4422255.5000
Epoch 13/100
 1/37 [..............................] - ETA: 0s - loss: 2399088.500037/37 [==============================] - 0s 2ms/step - loss: 4709955.7434 - val_loss: 4419829.5000
Epoch 14/100
 1/37 [..............................] - ETA: 0s - loss: 5605415.500037/37 [==============================] - 0s 2ms/step - loss: 5558924.8816 - val_loss: 4343293.0000
Epoch 15/100
 1/37 

In [0]:
model_path = "model"
model_name = "power_output_forecast"
model_uri = f"runs:/{run_id}/{model_path}" 

model_details = mlflow.register_model(model_uri=model_uri, name=model_name)

Registered model 'power_output_forecast' already exists. Creating a new version of this model...
2021/03/30 13:00:02 INFO mlflow.tracking._model_registry.client: Waiting up to 300 seconds for model version to finish creation. Model name: power_output_forecast, version 4
Created version '4' of model 'power_output_forecast'.

In [0]:
from mlflow.tracking.client import MlflowClient

mflow_client = MlflowClient()

mflow_client.transition_model_version_stage(
  name=model_details.name,
  version=model_details.version,
  stage='Production',
)

Out[30]: <ModelVersion: creation_timestamp=1617109202500, current_stage='Production', description='', last_updated_timestamp=1617109209073, name='power_output_forecast', run_id='23d4e110709446b48931ffe518cc6165', run_link='', source='dbfs:/databricks/mlflow-tracking/197254732634776/23d4e110709446b48931ffe518cc6165/artifacts/model', status='READY', status_message='', tags={}, user_id='7882912336567795', version='4'>